In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import json
import numpy as np
import scipy as sp
import scipy.stats as st
import scipy.integrate as integrate
from scipy.stats import multivariate_normal
from sklearn import linear_model
from sklearn.exceptions import ConvergenceWarning
import statsmodels.api as sm

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (15,8)
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('figure', **{'dpi': 300})

## Статистическая теория принятия решений

In [ ]:
## Оверфиттинг
## Исходная функция
orig = lambda x : np.sin(2*x)

## X-координаты точек данных
xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
num_points = len(xd)

## Данные
data = orig(xd) + np.random.normal(0, .25, num_points)

## Для рисования
xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)

## Выделение полиномиальных признаков
xs_d = np.vstack([xs ** i for i in range(1, num_points+1)]).transpose()
xd_d = np.vstack([xd ** i for i in range(1, num_points+1)]).transpose()

## Обучаем модель с регуляризацией
def train_model(xs, ys, alpha=0, use_lasso=False):
    if alpha == 0:
        return linear_model.LinearRegression(fit_intercept=True).fit( xs, ys )
    else:
        if use_lasso:
            return linear_model.Lasso(alpha=alpha, fit_intercept=True).fit( xs, ys )
        else:
            return linear_model.Ridge(alpha=alpha, fit_intercept=True).fit( xs, ys )

In [ ]:
N = 500

## Меняйте alpha для разной регуляризации
alpha =  0.01
use_lasso = False

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-3, 3))

res = []
for _ in range(N):
    cur_data = orig(xd) + np.random.normal(0, .25, num_points)
    cur_model = train_model(xd_d, cur_data, alpha, use_lasso)
    res.append(cur_model.predict( xs_d ))
    ax.plot(xs, res[-1], linewidth=.15, color="0.5")

ax.plot(xs, orig(xs), linewidth=2, label="Исходная функция", color=palette[0])
ax.scatter(xd, orig(xd), marker='*', s=150, color=palette[0])

ax.plot(xs, np.mean( res, axis=0 ), linewidth=2, label="Усреднённые предсказания", color="red")
ax.legend(loc="upper center", fontsize=legend_fontsize)
plt.show()

In [ ]:
test_set_size = 50
test_set_x = np.random.rand(test_set_size) * (2 + 1.5) - 1.5
test_set_xs = np.vstack([test_set_x ** i for i in range(1, 12)]).transpose()
print(test_set_xs.shape)
test_set_y = orig(test_set_xs[:,0]) + np.random.normal(0, .25, test_set_size)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.plot(xs, orig(xs), linewidth=2, label="Исходная функция", color=palette[0])
ax.scatter(test_set_xs[:,0], test_set_y, marker='*', s=150, color=palette[0])
ax.set_xlim((-1.5, 2))

def test_set_error(model, d):
    return np.mean( (test_set_y - model.predict(test_set_xs[:, :d])) ** 2 )

In [ ]:
N = 5000
use_lasso=False
alphas = np.logspace(-4, 2, num=20)
errors, biases, variances = [], [], []
for alpha in alphas:
    res, res_preds, res_test = [], [], []
    for _ in range(N):
        cur_data = orig(xd) + np.random.normal(0, .25, num_points)
        cur_model = train_model(xd_d, cur_data, alpha, use_lasso)
        res.append(test_set_error(cur_model, xd_d.shape[1]))
        res_test.append(cur_model.predict(test_set_xs))
        res_preds.append(cur_model.predict( xs_d ))
    res_test = np.array(res_test)
    avg_preds = np.mean(res_test, axis=0)
    errors.append(np.mean(res))
    biases.append(np.mean((avg_preds-orig(test_set_x))**2))
    variances.append(np.mean((res_test-avg_preds)**2))
    print("alpha = %.6f\tmean error = %.6f\tbias = %.6f\tvariance = %.6f" % (alpha, errors[-1], biases[-1], variances[-1]))

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
# plt.yscale('log')
plt.xscale('log')
ax.plot(alphas, biases, linewidth=2, label="Bias")
ax.plot(alphas, variances, linewidth=2, label="Variance")
ax.plot(alphas, np.array(biases) + np.array(variances), linewidth=2, label="Bias + Variance")
ax.plot(alphas, errors, linewidth=2, label="Ошибка на тестовом множестве", color="black")
ax.set_ylim((0, 1))
ax.set_xlim((0.001, 100))
ax.legend(fontsize=legend_fontsize)

## Байесовский вывод для гауссиана: фиксируем $\tau$

In [ ]:
data = np.random.normal(1, 0.5, 10)
xmin, xmax, ymax = -2, 3, 1.2
xs = np.arange(xmin, xmax, 0.01)

def plot_gaussian_with_center(ax, xs, loc, scale, label, color, linewidth=1):
    ax.plot(xs, st.norm.pdf(xs, loc=loc, scale=scale), label=label, color=color, linewidth=linewidth)
    ax.vlines(loc, 0, st.norm.pdf(loc, loc=loc, scale=scale), color=color, linestyle="--", linewidth=linewidth)
    
def plot_student_with_center(ax, xs, n, loc, scale, label, color, linewidth=2):
    ax.plot(xs, st.t.pdf(xs, n, loc=loc, scale=scale), label=label, color=color, linewidth=linewidth)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)
plot_gaussian_with_center(ax, xs, 1, .5, r"Истинное распределение: $\mathcal{N}(x|\mu=1, \tau=2)$", "black")
ax.scatter(data, np.random.rand(len(data))*0.0, marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
scale = 0.5
xmin, xmax = -5, 5
xs = np.arange(xmin, xmax, 0.01)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(20):
    ax.plot(xs, st.norm.pdf(xs, loc=np.random.normal(loc=0, scale=1), scale=scale), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=np.random.normal(loc=0, scale=1), scale=scale), color="0.3", linewidth=0.5, label=r"Выборка $\mu\sim\mathcal{N}(\mu|\mu_0=0,\tau_0=1)$")
    
ax.scatter(data[:2], np.zeros(2), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
def bayesian_update_mu(mu_0, tau_0, data, tau=2):
    tau_n = tau_0 + len(data)*tau
    mu_n = (tau_0 * mu_0 + tau*np.sum(data)) / tau_n
    return mu_n, tau_n

mu_0, tau_0 = 0, 1
mu_n, tau_n = bayesian_update_mu(mu_0, tau_0, data[:2])
print(mu_n, tau_n)

scale = 0.5
xmin, xmax = -5, 5
xs = np.arange(xmin, xmax, 0.01)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    plot_gaussian_with_center(ax, xs, np.random.normal(loc=mu_n, scale=np.sqrt(1/tau_n)), scale, None, "0.3", 0.35)

ax.plot(xs, st.norm.pdf(xs, loc=np.random.normal(loc=mu_n, scale=np.sqrt(1/tau_n)), scale=scale), color="0.3", linewidth=0.35, label=r"Выборка $\mu\sim\mathcal{N}(\mu|\mu_2\approx 0.4395,\tau_2=9)$")
    
ax.scatter(data[2:], np.zeros(len(data)-2), marker="*", s=120, label="Новые точки данных")
ax.scatter(data[:2], np.zeros(2), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
mu_m, tau_m = bayesian_update_mu(mu_n, tau_n, data[2:])
print(mu_n, tau_n)
print(mu_m, tau_m)

scale = 0.5
xmin, xmax = -5, 5
xs = np.arange(xmin, xmax, 0.01)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    plot_gaussian_with_center(ax, xs, np.random.normal(loc=mu_m, scale=np.sqrt(1/tau_m)), scale, None, "0.3", 0.35)

ax.plot(xs, st.norm.pdf(xs, loc=np.random.normal(loc=mu_m, scale=np.sqrt(1/tau_m)), scale=scale), color="0.3", linewidth=0.35, label=r"Выборка $\mu\sim\mathcal{N}(\mu|\mu_n\approx 0.9664,\tau_n=41)$")
    
ax.scatter(data[:2], np.zeros(2), marker="*", s=120, label="Точки данных")
ax.scatter(data[2:], np.zeros(len(data)-2), marker="*", s=120, label="Новые точки данных")
ax.set_xlim(xmin, xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

## Байесовский вывод для гауссиана: фиксируем $\mu$

In [ ]:
scale = 0.5
xmin, xmax = -5, 5
xs = np.arange(xmin, xmax, 0.01)
alpha_0, beta_0 = 1, 1

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_0, scale=1/beta_0))), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_0, scale=1/beta_0))), color="0.3", linewidth=0.5, label=r"Выборка $\tau\sim\mathrm{Gamma}(\tau|\alpha_0= %d,\beta_0=%d)$" % (alpha_0, beta_0))
ax.vlines(1, -1, 1.5, linewidth=.5, color="0.3", linestyle="--")
    
ax.scatter(data[:2], np.zeros(2), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
def bayesian_update_tau(alpha_0, beta_0, data, mu=1):
    alpha_n = alpha_0 + len(data)*0.5
    beta_n = beta_0 + 0.5 * np.sum((data-mu)**2)
    return alpha_n, beta_n

alpha_2, beta_2 = bayesian_update_tau(alpha_0, beta_0, data)
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_2, scale=1./beta_2))), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_2, scale=1./beta_2))), color="0.3", linewidth=0.5, label=r"Выборка $\tau\sim\mathrm{Gamma}(\tau|\alpha_n= %d,\beta_n\approx %.3f)$" % (alpha_2, beta_2))
ax.vlines(1, -1, 1.5, linewidth=.5, color="0.3", linestyle="--")
    
ax.scatter(data, np.zeros(len(data)), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
## Иллюстрация к зависимости между $\mu$ и $\sigma$

data2 = np.random.normal(1, 1, 20)
alpha_a, beta_a = bayesian_update_tau(alpha_0, beta_0, data2, mu=-1)
alpha_b, beta_b = bayesian_update_tau(alpha_0, beta_0, data2, mu=1)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    ax.plot(xs, st.norm.pdf(xs, loc=-1, scale=1/(np.random.gamma(shape=alpha_a, scale=1./beta_a))), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=-1, scale=1/(np.random.gamma(shape=alpha_a, scale=1./beta_a))), color="0.3", linewidth=0.5, label=r"Выборка $\tau\sim\mathrm{Gamma}(\tau|\alpha_n= %d,\beta_n\approx %.3f)$" % (alpha_a, beta_a))
ax.vlines(-1, -1, .5, linewidth=.5, color="0.3", linestyle="--")

ax.scatter(data2, np.zeros(len(data2)), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.02, .5)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_b, scale=1./beta_b))), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_b, scale=1./beta_b))), color="0.3", linewidth=0.5, label=r"Выборка $\tau\sim\mathrm{Gamma}(\tau|\alpha_n= %d,\beta_n\approx %.3f)$" % (alpha_b, beta_b))
ax.vlines(1, -1, .5, linewidth=.5, color="0.3", linestyle="--")

ax.scatter(data2, np.zeros(len(data2)), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, 1.5)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

## Байесовский вывод для гауссиана: обучаем и $\mu$, и $\tau$

In [ ]:
def p_mt(mu, tau, alpha, beta, mu_mu, lmb):
    return st.gamma.pdf(tau, alpha, scale = 1./beta) * st.norm.pdf(mu, loc=mu_mu, scale = 1./(lmb*tau))

def p_prior(mu, tau):
    return p_mt(mu, tau, 1., 1., 0, 1.)

zs_mu, zs_tau = np.arange(-3, 3, 0.025), np.arange(0.0001, 3, 0.025)
Z = np.array([[ p_prior(mu, tau) for mu in zs_mu] for tau in zs_tau])

In [ ]:
fig = plt.figure(figsize=(figsize[0]/1.5, figsize[1]/1.5))
ax = fig.add_subplot(111)
ax.set_xlim((-3, 3))
ax.set_ylim((0.02, 3))

heatmap = plt.pcolormesh(zs_mu, zs_tau, Z, cmap=plt.cm.jet)
plt.colorbar(heatmap, fraction=0.1)

In [ ]:
def bayesian_update_mt(alpha, beta, mu, lmb, data):
    n = len(data)
    lmb_n = lmb + n
    mu_n = (lmb*mu + np.sum(data)) / lmb_n
    alpha_n = alpha + n / 2.
    beta_n = lmb*mu*mu + np.sum(data ** 2) - (mu_n**2)*lmb_n
    return alpha_n, beta_n, mu_n, lmb_n

a, b, m, l = bayesian_update_mt(1., 1., 0., 1., data[:5])
Z = np.array([[ p_mt(mu, tau, a, b, m, l) for mu in zs_mu] for tau in zs_tau])

In [ ]:
fig = plt.figure(figsize=(figsize[0]/1.5, figsize[1]/1.5))
ax = fig.add_subplot(111)
ax.set_xlim((-3, 3))
ax.set_ylim((0.02, 3))

heatmap = plt.pcolormesh(zs_mu, zs_tau, Z, cmap=plt.cm.jet)
plt.colorbar(heatmap, fraction=0.1)

In [ ]:
def sample_mt(alpha, beta, mu, lmb):
    tau = np.random.gamma(shape=alpha, scale=1./beta)
    m = np.random.normal(loc=mu, scale=1./(lmb*tau))
    return m, tau

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    mu, t = sample_mt(1, 1, 0, 1)
    ax.plot(xs, st.norm.pdf(xs, loc=mu, scale=1/(t)), color="0.3", linewidth=0.5)

mu, t = sample_mt(1, 1, 0, 1)
ax.plot(xs, st.norm.pdf(xs, loc=mu, scale=1/t), color="0.3", linewidth=0.5, label=r"Выборка $\mu,\tau\sim p(\mu,\tau)$")
ax.vlines(1, -1, .5, linewidth=.5, color="0.3", linestyle="--")

ax.scatter(data[:5], np.zeros(len(data[:5])), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, 1.5)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

print(a,b,m,l)

for _ in range(10):
    mu, t = sample_mt(a, b, m, l)
    ax.plot(xs, st.norm.pdf(xs, loc=mu, scale=1/(t)), color="0.3", linewidth=0.5)

mu, t = sample_mt(a, b, m, l)
ax.plot(xs, st.norm.pdf(xs, loc=mu, scale=1/t), color="0.3", linewidth=0.5, label=r"Выборка $\mu,\tau\sim p(\mu,\tau|D)$")
ax.vlines(1, -1, .5, linewidth=.5, color="0.3", linestyle="--")

ax.scatter(data[:5], np.zeros(len(data[:5])), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, 1.5)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

## Распределение Стьюдента в апостериорном $p(\mu|x_1,\ldots,x_n)$

In [ ]:
mus = np.array([ sample_mt(a, b, m, l)[0] for _ in range(100000) ])
theta = st.t.fit(mus)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

ax.hist(mus, bins=200, linewidth=0.1, density=True, color="0.7")

xs = np.arange(-7, 5, 0.01)
ax.plot(xs, st.norm.pdf(xs, loc=np.mean(mus), scale=np.std(mus)), color=palette[0], linewidth=1.5, label="Нормальное распределение")
ax.plot(xs, st.t.pdf(xs, df=theta[0], loc=theta[1], scale=theta[2]), color=palette[2], linewidth=1.5, label="Распределение Стьюдента")
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

ax.hist(mus, bins=200, linewidth=0.1, density=True, color="0.7")

xs = np.arange(-7, 5, 0.01)
ax.plot(xs, st.norm.pdf(xs, loc=np.mean(mus), scale=np.std(mus)), color=palette[0], linewidth=1.5, label="Нормальное распределение")
ax.plot(xs, st.t.pdf(xs, df=theta[0], loc=theta[1], scale=theta[2]), color=palette[2], linewidth=1.5, label="Распределение Стьюдента")
ax.legend(loc="upper left", fontsize=legend_fontsize-2)
ax.set_ylim(0.0, 0.025)

## Распределение Стьюдента в апостериорном $p(x|x_1,\ldots,x_n)$

In [ ]:
mts = np.array([ sample_mt(a, b, m, l) for _ in range(100000) ])
new_xs = np.array([ np.random.normal(loc=params[0], scale=1./params[1]) for params in mts ])
theta = st.t.fit(new_xs)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

ax.hist(new_xs, bins=500, linewidth=0.1, density=True, color="0.7")

xs = np.arange(-20, 20, 0.1)
ax.plot(xs, st.norm.pdf(xs, loc=np.mean(new_xs), scale=np.std(new_xs)), color=palette[0], linewidth=1.5, label="Нормальное распределение")
ax.plot(xs, st.t.pdf(xs, df=theta[0], loc=theta[1], scale=theta[2]), color=palette[2], linewidth=1.5, label="Распределение Стьюдента")
ax.legend(loc="upper left", fontsize=legend_fontsize-2)
ax.set_xlim(-20, 20)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

ax.hist(new_xs, bins=500, linewidth=0.1, density=True, color="0.7")

xs = np.arange(-40, 40, 0.1)
ax.plot(xs, st.norm.pdf(xs, loc=np.mean(new_xs), scale=np.std(new_xs)), color=palette[0], linewidth=1.5, label="Нормальное распределение")
ax.plot(xs, st.t.pdf(xs, df=theta[0], loc=theta[1], scale=theta[2]), color=palette[2], linewidth=1.5, label="Распределение Стьюдента")
ax.legend(loc="upper left", fontsize=legend_fontsize-2)
ax.set_xlim(-20, 20)
ax.set_ylim(0.0, 0.025)